# EDA: GoEmotion Data sets (merged ones)

In [1]:
from pathlib import Path
from typing import *

In [2]:
import sys

PROJ_ROOT = Path().cwd().parent

if str(PROJ_ROOT) not in sys.path:
    sys.path.append(str(PROJ_ROOT))

In [3]:
import numpy as np
import pandas as pd
import scipy.stats as stats

In [4]:
import altair as alt


def adhoc_theme():
    theme_dict = {
        "config": {
            "view": {"height": 400, "width": 800},
            "title": {"fontSize": 24, "fontWeight": "normal", "titleAlign": "center"},
            "axisLeft": {"labelFontSize": 14, "titleFontSize": 16},
            "axisRight": {"labelFontSize": 14, "titleFontSize": 16},
            "header": {"labelFontSize": 14, "titleFontSize": 16, "titleAlign": "left"},
            "axisBottom": {"labelFontSize": 14, "titleFontSize": 16},
            "legend": {"labelFontSize": 12, "titleFontSize": 14},
            "range": {"category": {"scheme": "category10"}},
        }
    }
    return theme_dict


alt.themes.register("adhoc_theme", adhoc_theme)
alt.themes.enable("adhoc_theme")

alt.data_transformers.enable("default", max_rows=30000)
## needed for large data set

DataTransformerRegistry.enable('default')

## Data preprocessing

In [5]:
from lib.preprocessing import Preprocessor

preprocessor = Preprocessor(with_lemmtatization=False)

In [6]:
with pd.option_context("display.max_colwidth", None):
    display(preprocessor.df_train.sample(n=3, random_state=1))

LOADED: 43410 x 29


text  \
id                                                                                                       
efh3oek                                                                            I know the feeling.   
eczx96b  You seem slightly sensitive... I was actually thinking we had been infiltrated by the normies   
eekor8l                Instant fucking turn off, ugh. Fuck us for wanting equality across the spectrum   

         admiration  amusement  anger  annoyance  approval  caring  confusion  \
id                                                                              
efh3oek           0          0      0          0         0       0          0   
eczx96b           0          0      0          0         1       1          0   
eekor8l           0          0      1          0         0       0          0   

         curiosity  desire  ...  love  nervousness  optimism  pride  \
id                          ...                                       
efh3oek          0       0  ...     0            0         0      0   
eczx96b          0       0  ...     0            0         0      0   
eekor8l          0       0  ...     0            0         0      0   

         realization  relief  remorse  sadness  surprise  neutral  
id                                                                 
efh3oek            0       0        0        0         0        1  
eczx96b            0       0        0        0         0        0  
eekor8l            0       0        0        0         0        0  

[3 rows x 29 columns]

In [7]:
preprocessor.count_emotions()

n_label  n_text   pct_text
0        1   36308  83.639714
1        2    6541  15.067957
2        3     532   1.225524
3        4      28   0.064501
4        5       1   0.002304

In [8]:
preprocessor.bar_chart_label_proportion()

alt.Chart(...)

In [9]:
%%time

preprocessor.bar_chart_count_docs_by_length()

CPU times: user 4.24 s, sys: 7.65 ms, total: 4.24 s
Wall time: 4.24 s


alt.Chart(...)

In [10]:
preprocessor.heatmap_label_correlation()

alt.Chart(...)

### Signal words

Here a signal word is a text token which increases the proportion of a specific label. In other words it is a token with high conditional probability `P(label|token)`.

In [11]:
%%time

# preprocessor.histogram_positive_rate()  ## around 3 min

CPU times: user 4 µs, sys: 0 ns, total: 4 µs
Wall time: 8.34 µs


In [12]:
%%time

# preprocessor.bar_chart_of_top5_signal_words()

CPU times: user 5 µs, sys: 1e+03 ns, total: 6 µs
Wall time: 11.4 µs


## Baseline model with TFIDF

In [13]:
X_train, Y_train = preprocessor.get_train_X_and_Y()
X_train.shape, Y_train.shape

((43410,), (43410, 28))

In [14]:
from emo_classifier.model import TfidfClassifier

tfidf_classifier = TfidfClassifier(tokenizer=preprocessor.tokenizer, min_df=43)

In [15]:
from sklearn.linear_model import LogisticRegression

param_grid = {"C": [0.1, 1.0, 10, 100]}
tfidf_classifier.set_model(
    "plr", LogisticRegression(random_state=0, solver="liblinear", fit_intercept=False), param_grid
)

In [16]:
%%time

tfidf_classifier.fit(X_train, Y_train)

CPU times: user 6.7 s, sys: 192 ms, total: 6.89 s
Wall time: 42.5 s


rank_test_score  mean_test_score  std_test_score  mean_train_score  \
2                1         0.287604        0.005908          0.320848   
3                2         0.285071        0.004004          0.338429   
1                3         0.266020        0.005101          0.282883   
0                4         0.200151        0.002492          0.205471   

   mean_fit_time param_estimator__C  
2      14.692958                 10  
3      18.278310                100  
1       6.686909                1.0  
0       3.757310                0.1

In [17]:
%%time

Y_hat = tfidf_classifier.predict_proba(X_train)
Y_hat.shape

CPU times: user 2.65 s, sys: 3.75 ms, total: 2.66 s
Wall time: 2.65 s


(43410, 28)

In [18]:
idx2label = preprocessor.emotions

(
    alt.Chart(pd.DataFrame(Y_hat, columns=idx2label, index=preprocessor.df_train.index).sample(n=5000))
    .transform_fold(fold=idx2label, as_=["emotion", "probability"])
    .mark_bar()
    .encode(
        x=alt.X("probability:Q", bin=alt.Bin(maxbins=30), axis=alt.Axis(format="%"), title=None),
        y=alt.Y("count():Q", title=None),
        facet=alt.Facet("emotion:N", columns=6),
    )
    .properties(width=120, height=100, title="Histogram of predictions")
)

alt.Chart(...)

In [19]:
tfidf_classifier.save()

SAVED: /home/stdiff/Entwicklung/Python/68-emo-classifier/emo_classifier/data/TfidfClassifier.joblib


## Evaluation of the model on the dev set

In [20]:
tfidf_classifier = TfidfClassifier.load()

LOADED: TfidfClassifier instance


In [21]:
%%time

X_dev, Y_dev = preprocessor.get_dev_X_and_Y()
Y_hat_dev = tfidf_classifier.predict_proba(X_dev)

LOADED: 5426 x 29
CPU times: user 832 ms, sys: 0 ns, total: 832 ms
Wall time: 840 ms


In [22]:
from lib.evaluation import PredictionOnDevSetEvaluator

evaluator_dev = PredictionOnDevSetEvaluator(Y_true=Y_dev, Y_prob=Y_hat_dev, X_text=preprocessor.df_dev["text"])
thresholds = evaluator_dev.thresholds()
thresholds.save()

SAVED: /home/stdiff/Entwicklung/Python/68-emo-classifier/emo_classifier/data/Thresholds.json


In [23]:
evaluator_dev.macro_f1_score()

0.3348767073014497

In [24]:
evaluator_dev.best_thresholds.sort_values(by="f1_score", ascending=False)

label  threshold  precision    recall  f1_score  positive_rate  \
15       gratitude   0.543539   0.930599  0.824022  0.874074       0.058238   
1        amusement   0.506422   0.772926  0.584158  0.665414       0.042020   
20         neutral   0.303547   0.511548  0.840317  0.635955       0.018430   
18            love   0.536678   0.718593  0.567460  0.634146       0.036491   
0       admiration   0.534125   0.732026  0.459016  0.564232       0.056211   
14            fear   0.530732   0.687500  0.366667  0.478261       0.008662   
21        optimism   0.502713   0.722772  0.349282  0.470968       0.000553   
25         remorse   0.535240   0.709677  0.323529  0.444444       0.012532   
22           pride   0.573901   1.000000  0.266667  0.421053       0.003686   
26         sadness   0.527744   0.608696  0.293706  0.396226       0.009031   
8           desire   0.747894   0.833333  0.259740  0.396040       0.004239   
11         disgust   0.755984   0.694444  0.257732  0.375940       0.006450   
17             joy   0.513160   0.625000  0.261628  0.368852       0.013085   
27        surprise   0.507719   0.540000  0.209302  0.301676       0.534464   
2            anger   0.502586   0.487805  0.205128  0.288809       0.014928   
13      excitement   0.545595   0.437500  0.145833  0.218750       0.004976   
4         approval   0.106219   0.125000  0.523929  0.201844       0.306487   
3        annoyance   0.190613   0.132754  0.353135  0.192967       0.148360   
7        curiosity   0.169583   0.128169  0.366935  0.189979       0.130483   
6        confusion   0.539217   0.531250  0.111842  0.184783       0.005713   
10     disapproval   0.083900   0.095872  0.493151  0.160535       0.276631   
19     nervousness   0.788402   0.500000  0.095238  0.160000       0.000553   
23     realization   0.556289   0.523810  0.086614  0.148649       0.000000   
12   embarrassment   0.567228   0.500000  0.085714  0.146341       0.000921   
5           caring   0.564905   0.500000  0.084967  0.145251       0.004055   
16           grief   0.515938   0.500000  0.076923  0.133333       0.000184   
24          relief   0.542634   0.250000  0.055556  0.090909       0.005529   
9   disappointment   0.102594   0.051310  0.288344  0.087118       0.168633   

    actual_positive_rate  
15              0.065979  
1               0.055842  
20              0.038518  
18              0.046443  
0               0.089937  
14              0.016587  
21              0.002764  
25              0.026355  
22              0.023406  
26              0.023774  
8               0.014191  
11              0.017877  
17              0.031699  
27              0.325470  
2               0.035938  
13              0.017693  
4               0.073166  
3               0.055842  
7               0.045706  
6               0.028013  
10              0.053815  
19              0.003870  
23              0.003317  
12              0.006450  
5               0.028198  
16              0.002396  
24              0.012532  
9               0.030041

In [25]:
evaluator_dev.metrics_scatter_plot()

alt.LayerChart(...)

In [26]:
evaluator_dev.positive_rate_scatter_plot()

alt.LayerChart(...)

In [27]:
with pd.option_context("display.max_colwidth", None):
    display(evaluator_dev.false_positive_by_label().sort_values(by="label").head(18))

probability       label  \
id                                 
ef3huhl     0.994957  admiration   
eepgcla     0.997405  admiration   
ee6qx9u     0.999323  admiration   
eczvsr7     0.999426   amusement   
ef1l5oh     0.999999   amusement   
ef0v8ga     0.998464   amusement   
edp0uwr     0.961293       anger   
edu6hca     0.978501       anger   
ed5bb5g     0.955163       anger   
eevz90x     0.904581   annoyance   
eeq6hyt     0.882259   annoyance   
ee5gmhs     0.979005   annoyance   
ee3rdp6     0.996127    approval   
eem5vrq     0.954313    approval   
eeq9i4h     0.861136    approval   
edjhxf2     0.838977      caring   
edqz53f     0.838977      caring   
ed04ap3     0.839194      caring   

                                                                                                                        text  \
id                                                                                                                             
ef3huhl               Georgetown - great food, great shops/ the "exorcist" steps are located there, too. the exorcist steps    
eepgcla                                                                                             That really is fantastic   
ee6qx9u                                                                               This is beautiful and heartbreaking :(   
eczvsr7                                                                                         No, this sub adores puig lol   
ef1l5oh                                                                                 It’s neither. It’s an acrostic, lol.   
ef0v8ga                                                                                                      Lol! Exactly. ☹   
edp0uwr                                                                       I'd rather be bitter and angry than miserable.   
edu6hca                                                       For fuck sake... just go and remind them it's the quiet train!   
ed5bb5g                                                                                                 Oil barons hate him!   
eevz90x                                                                                             This is full of bullshit   
eeq6hyt                                                                                                   That seems stupid.   
ee5gmhs  Will quickly be removed from lobby screen but the game mode selection button will keep the annoying warning/advert.   
ee3rdp6                                                                                                 Couldn't agree more.   
eem5vrq                                                                                                  Couldnt agree more.   
eeq9i4h                                                             Agreed. And I like how far you can see into the distance   
edjhxf2                                                                                          Filthy. Stay there, please.   
edqz53f                                                                       I picked it so it forced me to stay anonymous.   
ed04ap3                                                                                        We'll worry about it tomorrow   

                   true_labels  
id                              
ef3huhl                neutral  
eepgcla             excitement  
ee6qx9u                sadness  
eczvsr7                neutral  
ef1l5oh                neutral  
ef0v8ga               approval  
edp0uwr                neutral  
edu6hca              annoyance  
ed5bb5g  annoyance,disapproval  
eevz90x                  anger  
eeq6hyt            disapproval  
ee5gmhs                neutral  
ee3rdp6            disapproval  
eem5vrq            disapproval  
eeq9i4h                neutral  
edjhxf2                disgust  
edqz53f                neutral  
ed04ap3                neutral

In [28]:
with pd.option_context("display.max_colwidth", None):
    display(evaluator_dev.false_negative_by_label().sort_values(by="label").head(18))

probability       label  \
id                                 
eed6tft     0.002895  admiration   
ed412mo     0.002601  admiration   
eda2ojj     0.005235  admiration   
eewao3i     0.002276   amusement   
edcqbz0     0.001920   amusement   
eej85k7     0.001720   amusement   
edrhoxh     0.002255       anger   
ef8scux     0.002446       anger   
ee1cn14     0.001603       anger   
eda8pj6     0.002231   annoyance   
ee0tttf     0.001480   annoyance   
ed2znun     0.000516   annoyance   
ee9ux5b     0.003921    approval   
eeey7os     0.004422    approval   
ef4xaa7     0.003878    approval   
ef8qnpp     0.002926      caring   
ed46uxg     0.001104      caring   
ee56aa4     0.002182      caring   

                                                                                                                                                          text  \
id                                                                                                                                                               
eed6tft        Nukeville sounds like a nicer neighborhood. Like no broken and burnt houses and like children playing in the street and people having barbecues   
ed412mo        Yeah people that take money from their children don't just look at their Bank account and think "Wow a 4000 dollar deposit magically happened."   
eda2ojj                                                                                                                                  Sick burn. I like it.   
eewao3i                                A thousand times this! I just found some of my old childhood stuff from the 80s with a 2 bar and it is fucking awesome.   
edcqbz0                                                                                   so true cuz i’m pretty miserable but my instagram life looks amazing   
eej85k7                                                                    I love it when people barge into my house and demand to know why I don't like them.   
edrhoxh   The FDA has plenty to criticize. But like here, it's usually criticized horribly off base. It needs to grow some balls and actually enforce things.    
ef8scux                      I'm honestly so pissed off for you. That whole situation is insane. Good luck moving on. No one deserves to be treated like that.   
ee1cn14         Ha, who cares about them supporters...the most important thing for society is that justice is served and the man jailed! Scream all you want.    
eda8pj6                                        You cant love this girl if she already has a GF whom she sounds like she loves. You'll just ruin a relationship   
ee0tttf                                  Yeah, I always get about 6 episodes deep and then start hate-watching just to see if they ever actually fall in love.   
ed2znun  Lol dream on buddy. You’ve had enough attention today. Actually learn what your talking about helps a lot. Sorry your stuck in free roam smokin crack   
ee9ux5b                                                           Ah damn, I forgot the /s, a AAA company would never put out a half-finished game. Good catch   
eeey7os                                                                                        thanks, metropolitan looks legit according to google searches.    
ef4xaa7               Reminds me of that Australian news story about kids addicted to Fortnite and the kid is talking about how much he loves [NAME] ([NAME]).   
ef8qnpp   [NAME] is having a hard time moving on. [NAME] need to cash in with AD before the trade deadline, because his value is going down after this season.   
ed46uxg                                I'm with you. I'd love for my nex to read what I post. It probably wouldn't matter because she has zero self-awareness.   
ee56aa4                                                                                             I just call my girl and tell her I love her lol. Easy day.   

                                true_labels  
i

## Model evaluation on the test set

In [29]:
%%time

X_test, Y_test = preprocessor.get_test_X_and_Y()
Y_hat_test = tfidf_classifier.predict_proba(X_test)

LOADED: 5427 x 29
CPU times: user 776 ms, sys: 0 ns, total: 776 ms
Wall time: 771 ms


In [30]:
from lib.evaluation import PredictionOnTestSetEvaluator

evaluator_test = PredictionOnTestSetEvaluator(Y_true=Y_test, Y_prob=Y_hat_test, thresholds=thresholds)

In [31]:
from lib.evaluation import PredictionOnTestSetEvaluator

evaluator_test = PredictionOnTestSetEvaluator(Y_true=Y_test, Y_prob=Y_hat_test, thresholds=thresholds)
evaluator_test.macro_f1_score()

/home/stdiff/.cache/pypoetry/virtualenvs/emo-classifier-BHO4KP39-py3.9/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1248: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


0.2961275045626222

In [32]:
evaluator_test.metrics_scatter_plot()

alt.LayerChart(...)

In [33]:
evaluator_test.positive_rate_scatter_plot()

alt.LayerChart(...)

## Environment

In [34]:
%load_ext watermark
%watermark -v -n -m -p numpy,scipy,sklearn,pandas,matplotlib,seaborn,altair,torch

Python implementation: CPython
Python version       : 3.9.1
IPython version      : 7.30.0

numpy     : 1.21.4
scipy     : 1.7.3
sklearn   : 0.24.2
pandas    : 1.3.4
matplotlib: not installed
seaborn   : not installed
altair    : 4.1.0
torch     : 1.9.1

Compiler    : GCC 7.3.0
OS          : Linux
Release     : 5.3.18-59.34-default
Machine     : x86_64
Processor   : x86_64
CPU cores   : 8
Architecture: 64bit

